In [11]:
from web3 import Web3
from hexbytes import HexBytes
import pandas as pd
import numpy as np
import rlp
import requests
from web3 import Web3
#from dotenv import load_dotenv

from datetime import datetime, timedelta, timezone

import matplotlib.pylab as plt
import numpy as np
import json
import logging
import typing
import requests
import sys
import time

import pandas as pd
import seaborn as sns
from web3 import Web3
#load_dotenv()

In [12]:

root = logging.getLogger()
root.setLevel(logging.INFO)

handler = logging.StreamHandler(sys.stdout)
handler.setLevel(logging.INFO)
formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')
handler.setFormatter(formatter)
root.addHandler(handler)

In [13]:
def empty_labels() -> pd.DataFrame:
        df_forta = pd.DataFrame(columns=['createdAt', 'id', 'label', 'source'])
        return df_forta

def labels_by_source_id(source_id: str, start_date: datetime, end_date: datetime) -> pd.DataFrame:
    url = "https://api.forta.network/graphql"
    chunk_size = 8000

    df_forta = empty_labels()
    json_data = ""
    first_run = True
    count = 0
    while (json_data == "" or json_data['data']['labels']['pageInfo']['hasNextPage']):
        query = """query exampleQuery {
                    labels(
                        input: {
                            SOURCEIDS_CLAUSE
                            CREATEDBEFORE_CLAUSE
                            CREATEDSINCE_CLAUSE
                            AFTER_CLAUSE
                            CHUNKSIZE
                            state: true
                        }
                    ) {
                        pageInfo {
                            endCursor {
                                pageToken
                            }
                            hasNextPage
                        }
                        labels {
                            createdAt
                            id
                            label {
                                label
                                metadata
                                remove
                                entityType
                                entity
                                confidence
                            }
                            source {
                                chainId
                                alertId
                            }
                        }
                    }
                }"""

        after_clause = ""
        if(first_run is False):
            pageToken = json_data['data']['labels']['pageInfo']['endCursor']['pageToken']
            after_clause = """after: {{pageToken:"{0}"}}""".format(pageToken)

        # this is a bit hacky
        query = query.replace("SOURCEIDS_CLAUSE", f"""sourceIds: ["{source_id}"]""")
        query = query.replace("CREATEDBEFORE_CLAUSE", f"""createdBefore: {int(end_date.timestamp()*1000)}""")
        query = query.replace("CREATEDSINCE_CLAUSE", f"""createdSince: {int(start_date.timestamp()*1000)}""")
        query = query.replace("AFTER_CLAUSE", after_clause)
        query = query.replace("CHUNKSIZE", f"first: {chunk_size}") 

        #print(query)

        retries = 1
        wait = 1
        success = False
        while not success:
            try:
                count += 1
                r = requests.post(url, json={'query': query})
                if r.status_code == 200:
                    success = True
                    if chunk_size < 5000:
                        chunk_size *= 2
                        logging.warning(f"Increasing chunk size to {chunk_size}")
                else:
                    raise Exception(f"status code: {r.status_code} {r.text}")
            except Exception as e:
                logging.warning(f"Unable to retrieve alerts {r.status_code} , {e}")
                logging.warning(f"Sleeping {wait}sec. Count {count}.")
                old_chunk_size = chunk_size
                chunk_size = int(chunk_size/2)
                if(chunk_size<1):
                    chunk_size = 1
                query = query.replace(f"first: {old_chunk_size},", f"first: {chunk_size},") 
                logging.warning(f"Reducing chunk size to {chunk_size}")
                time.sleep(wait)
                retries += 1
                if retries > 30:
                    raise Exception("Unable to retrieve alerts even after repeated retries. Pls check logs")

        json_data = json.loads(r.text)
        df_data = json_data['data']['labels']['labels']
        df_forta = pd.concat([pd.DataFrame(df_data), df_forta])

        first_run = False
        count += 1

    return df_forta


In [26]:
source_id = "0x6f022d4a65f397dffd059e269e1c2b5004d822f905674dbf518d968f744c2ede"
start_date = datetime(2012, 3, 1, 0, 0, 0, 0, timezone.utc)
end_date = datetime(2023, 3, 31, 0, 0, 0, 0, timezone.utc)


In [27]:
df_forta_labels = empty_labels()
#df_etherscan_labels1 = labels_by_source_id("etherscan", start_date, end_date)
#print(len(df_etherscan_labels1))
df_forta_labels = labels_by_source_id(source_id, start_date, end_date)
print(len(df_forta_labels))
#df_forta_labels = pd.concat([df_etherscan_labels1, df_etherscan_labels2])

14718


In [28]:
df_forta_labels

createdAt  \
0     2023-03-22T15:41:37.814467005Z   
1     2023-03-22T15:42:09.550977088Z   
2     2023-03-22T15:42:09.550977088Z   
3     2023-03-22T15:42:09.550977088Z   
4     2023-03-22T15:42:09.550977088Z   
...                              ...   
7995  2023-03-22T15:41:37.814467005Z   
7996  2023-03-22T15:41:37.814467005Z   
7997  2023-03-22T15:41:37.814467005Z   
7998  2023-03-22T15:41:37.814467005Z   
7999  2023-03-22T15:41:37.814467005Z   

                                                     id  \
0     0x4ca1a729dd65cfc7e42774252a41668177c380a98618...   
1     0x82486fe4a15c651c9d41ccd11d7ad580258e5c599bf6...   
2     0x6e5642e2f01d889fb3a332060e90262f8f9ac2ec8159...   
3     0x2ef9dd6efa4a1981bf0c6125ac5f500c316f5b71fc72...   
4     0x877017f8e3b58c4c6a5d21e2317f1422ccdef8efbbde...   
...                                                 ...   
7995  0x6aca3afc9080ed6db7627b70dfa7d5f7aa5702d39ce7...   
7996  0x97434a318c034cf4d9b854f7f6e7c4d0c992e56cc164...   
7997  0x10e46189051331201fc720eebe6b647c7c44ace31a66...   
7998  0x9cfeea89b84e322e74d93afeea07d8c0cf0a39a73f98...   
7999  0x14615544dea1b051e62bfc9ae7caa470909ee69f0f9a...   

                                                  label  \
0     {'label': 'uniswap', 'metadata': None, 'remove...   
1     {'label': 'uniswap', 'metadata': None, 'remove...   
2     {'label': 'artificial intelligence', 'metadata...   
3     {'label': 'token contract', 'metadata': None, ...   
4     {'label': 'name|uniswap v2: afy 2', 'metadata'...   
...                                                 ...   
7995  {'label': 'name|merit circle: mc token', 'meta...   
7996  {'label': 'play-to-earn', 'metadata': None, 'r...   
7997  {'label': 'token contract', 'metadata': None, ...   
7998  {'label': 'name|uniswap v2: mc 6', 'metadata':...   
7999  {'label': 'gaming', 'metadata': None, 'remove'...   

                                          source  
0     {'chainId': None, 'alertId': 'label-sync'}  
1     {'chainId': None, 'alertId': 'label-sync'}  
2     {'chainId': None, 'alertId': 'label-sync'}  
3     {'chainId': None, 'alertId': 'label-sync'}  
4     {'chainId': None, 'alertId': 'label-sync'}  
...                                          ...  
7995  {'chainId': None, 'alertId': 'label-sync'}  
7996  {'chainId': None, 'alertId': 'label-sync'}  
7997  {'chainId': None, 'alertId': 'label-sync'}  
7998  {'chainId': None, 'alertId': 'label-sync'}  
7999  {'chainId': None, 'alertId': 'label-sync'}  

[14718 rows x 4 columns]

In [29]:
df_labels = pd.DataFrame(columns=['createdAt', 'entity', 'entityType', 'label', 'chain_id', 'confidence', 'remove', 'alert_id'])

for index, row in df_forta_labels.iterrows():
    created_date = row['createdAt']
    source = row['source']
    #print(source)
    alert_id = source['alertId']
    chain_id = source['chainId']
    label = row['label']
    entity = label['entity']
    entityType = label['entityType']
    label_tag = label['label']
    remove = label['remove']
    confidence = label['confidence']
    df_temp_labels = pd.DataFrame(columns=['createdAt', 'entity', 'entityType', 'label', 'chain_id', 'confidence', 'remove', 'alert_id'], data=[[created_date, entity, entityType, label_tag, chain_id, confidence, remove, alert_id]])
    df_labels = pd.concat([df_labels, df_temp_labels])

/var/folders/p5/4m340z515tsdn8mxjy2_r1ph0000gn/T/ipykernel_49258/3400230709.py:16: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_labels = pd.concat([df_labels, df_temp_labels])
/var/folders/p5/4m340z515tsdn8mxjy2_r1ph0000gn/T/ipykernel_49258/3400230709.py:16: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_labels = pd.concat([df_labels, df_temp_labels])
/var/folders/p5/4m340z515tsdn8mxjy2_r1ph0000gn/T/ipykernel_49258/3400230709.py:16: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_labels = pd.concat([df_labels, df_temp_labels])
/var/folders/p5/4m340z515tsdn8mxjy2_r1ph0000gn/T/ipykernel_49258/34002307

In [30]:
df_labels['createdAt'] = pd.to_datetime(df_labels['createdAt'])  # Ensure the 'date' column is in datetime format
df_sorted = df_labels.sort_values(by='createdAt')  # Sort DataFrame by 'date' column
df_labels_deduplicated = df_sorted.drop_duplicates(subset=['entity', 'chain_id'], keep='first')

In [31]:
df_labels_deduplicated

createdAt  \
0  2023-01-07 18:38:31.000640843+00:00   
0  2023-01-07 19:51:56.552432051+00:00   
0  2023-01-07 21:38:11.448101986+00:00   
0  2023-01-07 23:33:15.249335524+00:00   
0  2023-01-07 23:33:15.249335524+00:00   
..                                 ...   
0  2023-03-30 23:48:05.536703037+00:00   
0  2023-03-30 23:50:53.342364076+00:00   
0     2023-03-30 23:52:16.976753+00:00   
0  2023-03-30 23:53:42.566609863+00:00   
0  2023-03-30 23:53:42.566609863+00:00   

                                        entity entityType  \
0   0xa9cfc982a66d0134fee2539cfd633559fb5cf9a0    ADDRESS   
0   0xeb45156afec97cbfd51f0464251e044ed4689c72    ADDRESS   
0   0xb70f65c1faa2f1160d006b585ebf564781e8dae6    ADDRESS   
0   0xa70d0709987c5a27f2bac0f39abbc4d8cf6d03b4    ADDRESS   
0   0x38f4f4bce203b557d82bf0e5e731b58b9935ed31    ADDRESS   
..                                         ...        ...   
0   0x69cdc3245c714a6b99cea9b43869e2b893a031ad    ADDRESS   
0   0xb948f35c1c35206a5fb23b77f9e52a01b793c909    ADDRESS   
0   0xc78fa2af0ca7990bb5ff32c9a728125be58cf247    ADDRESS   
0   0x1c4853ec0d55e420002c5efabc7ed8e0ba7a4121    ADDRESS   
0   0x5ad7452ceafdaeb0936507d5bb5890964ef56bd3    ADDRESS   

                            label chain_id confidence remove  \
0                    phish / hack     None          1  False   
0                    phish / hack     None          1  False   
0                    phish / hack     None          1  False   
0                    phish / hack     None          1  False   
0                    phish / hack     None          1  False   
..                            ...      ...        ...    ...   
0   name|baby moon owls: deployer     None          1  False   
0          name|mintify: deployer     None          1  False   
0        name|stake dao: deployer     None          1  False   
0    name|kanagawa nami: deployer     None          1  False   
0    name|kanagawa nami: deployer     None          1  False   

               alert_id  
0   risky-address-label  
0   risky-address-label  
0   risky-address-label  
0   risky-address-label  
0   risky-address-label  
..                  ...  
0            label-sync  
0            label-sync  
0            label-sync  
0            label-sync  
0            label-sync  

[9051 rows x 8 columns]

In [20]:
df_labels_deduplicated.to_csv("202303_etherscan_labels.csv")

In [30]:
# label_api = "https://api.forta.network/labels/events?sourceIds=etherscan&labels=phish"
# results = []
# while 'pageToken' in results or results == []:
#     pageToken = '&pageToken=' + str(results['pageToken']) if 'pageToken' in results else ''
#     results = requests.get(label_api + pageToken).json()
#     for result in results['events']:
#         created_at = datetime.strptime(result['created_at'][0:10],"%Y-%m-%d")
#         if(created_at>=start_date and created_at<=end_date):
#             if result['label']['label'] == 'phish-hack':
#                 print(result['created_at'][0:10] + ',' + result['label']['entity'])